In [15]:
import pandas as pd
import numpy as np
import json
from sklearn.model_selection import train_test_split

In [16]:
songs_df = pd.read_csv('final_cleaned.csv')
print(songs_df.shape)

(13640, 6)


In [17]:
songs_df.head()

id                                             lyrics  \
0  4575103  [Chorus: Ed Sheeran]\nOh, I been on for a thou...   
1  3541694  [Verse 1]\nI will always remember\nThe day you...   
2  7120781  [Verse 1]\nI had a bad week\nSpent the evening...   
3  7921365  [Verse 1: Ed Sheeran]\nI had a bad week\nSpent...   
4   493576  [Verse 1]\nI think I took too much\nI'm addict...   

                                          annotation      artist  artist_id  \
0  “1000 Nights” is a collaboration between Ed Sh...  Ed Sheeran      12418   
1  In “2002,” Anne-Marie reminisces about falling...  Ed Sheeran      12418   
2  In an upbeat switch of tone, “2step” is Ed She...  Ed Sheeran      12418   
3  “2step (Remix)” is the fifth single from Ed Sh...  Ed Sheeran      12418   
4  Ed mentions in the Part 2 of his tour diary th...  Ed Sheeran      12418   

            song  
0    1000 Nights  
1           2002  
2          2step  
3  2step (Remix)  
4       Addicted

In [18]:
def create_prompts_table(data, pre_text, post_text):
    pre_prompt = pre_text
    main_prompt = data['annotation']
    post_prompt = post_text
    full_prompt = pre_prompt + main_prompt + post_prompt
    return full_prompt

In [19]:
#create a sampel prompts table
pre = pd.DataFrame(["Write me a song called "] * songs_df.shape[0])[0] + songs_df['song'] + ' with the following description: '
post = pd.DataFrame([" Make sure the lyrics are different from the original song."] * songs_df.shape[0])[0]
prompt = create_prompts_table(songs_df, pre, post)
prompts_df = pd.DataFrame({'prompts': prompt})
prompts_df.head()

prompts
0  Write me a song called 1000 Nights with the fo...
1  Write me a song called 2002 with the following...
2  Write me a song called 2step with the followin...
3  Write me a song called 2step (Remix) with the ...
4  Write me a song called Addicted with the follo...

In [20]:
prompts_df['prompts'][0]

'Write me a song called 1000 Nights with the following description: “1000 Nights” is a collaboration between Ed Sheeran, Meek Mill, and A Boogie wit da Hoodie that appears on Ed’s No.6 Collaborations Project. On the track, the artists discuss touring the world and boast about the perks of being rich and famous.\nThis songs marks the first time any of these artists have collaborated. Make sure the lyrics are different from the original song.'

In [21]:
songs_df["prompts"] = prompts_df["prompts"]
songs_df.head()

id                                             lyrics  \
0  4575103  [Chorus: Ed Sheeran]\nOh, I been on for a thou...   
1  3541694  [Verse 1]\nI will always remember\nThe day you...   
2  7120781  [Verse 1]\nI had a bad week\nSpent the evening...   
3  7921365  [Verse 1: Ed Sheeran]\nI had a bad week\nSpent...   
4   493576  [Verse 1]\nI think I took too much\nI'm addict...   

                                          annotation      artist  artist_id  \
0  “1000 Nights” is a collaboration between Ed Sh...  Ed Sheeran      12418   
1  In “2002,” Anne-Marie reminisces about falling...  Ed Sheeran      12418   
2  In an upbeat switch of tone, “2step” is Ed She...  Ed Sheeran      12418   
3  “2step (Remix)” is the fifth single from Ed Sh...  Ed Sheeran      12418   
4  Ed mentions in the Part 2 of his tour diary th...  Ed Sheeran      12418   

            song                                            prompts  
0    1000 Nights  Write me a song called 1000 Nights with the fo...  
1           2002  Write me a song called 2002 with the following...  
2          2step  Write me a song called 2step with the followin...  
3  2step (Remix)  Write me a song called 2step (Remix) with the ...  
4       Addicted  Write me a song called Addicted with the follo...

In [29]:
def convert_table_to_conversation(data):
    result = []
    for i in range(data.shape[0]):
        row = data.iloc[i]
        outer_dict = {}
        outer_dict["id"] = i
        outer_dict["conversations"] = []
        conversations = outer_dict["conversations"]
        conversations.append({"from":"human", "value":row["prompts"]})
        conversations.append({"from":"gpt", "value":row["lyrics"]})
        result.append(outer_dict)
    return result

In [24]:
train_df, test_df = train_test_split(songs_df, test_size=.05)

In [33]:
train = convert_table_to_conversation(train_df)
train_json = json.dumps(train, indent=2)

In [34]:
test = convert_table_to_conversation(test_df)
test_json = json.dumps(test, indent=2)

In [35]:
print(train_json[0:100000])

[
  {
    "id": 0,
    "conversations": [
      {
        "from": "human",
        "value": "Write me a song called Night of Your Life with the following description: \u201cNight of Your Life\u201d is a song by David Guetta featuring Jennifer Hudson, for his album Nothing but the Beat. The song was released digitally on August 22, 2011, as the third and final promotional single from the album, as part of the iTunes Store\u2019s countdown to the album\u2019s release. Though released as a promo single, the song peaked at #81 on the Billboard Hot 100.\nLyrically, the song is about Jennifer Hudson wanting to be worshiped like the queen that she is. Make sure the lyrics are different from the original song."
      },
      {
        "from": "gpt",
        "value": "[Verse 1: Jennifer Hudson]\nBoy, I see ya, lookin' at me\nI feel your eyes on me, like you gotta have me\nWatchin' every move, like it's for you\nYou can't help it, you're attracted like a magnet\nMy love ain't easy\nYou gon' hav

In [37]:
# Write convo to conversation_style.json
with open("train/conversation_style.json", "w") as outfile:
    outfile.write(train_json)
    
with open("test/conversation_style.json", "w") as outfile:
    outfile.write(test_json)